In [1]:
using Revise;
includet("../experiment/ringworld.jl")

┌ Info: Precompiling ActionRNNs [8317d1c6-c5c3-11e9-1282-0f8c4be94ea0]
└ @ Base loading.jl:1260


OMEinsum: YOU FIND CUDA!


┌ Warning: Error requiring CuArrays from OMEinsum:
│ LoadError: LoadError: UndefVarError: mapreducedim_kernel_parallel not defined
│ Stacktrace:
│  [1] getproperty(::Module, ::Symbol) at ./Base.jl:26
│  [2] top-level scope at /Users/Matt/.julia/packages/OMEinsum/0rZnI/src/cudapatch.jl:10
│  [3] include(::Module, ::String) at ./Base.jl:377
│  [4] include(::String) at /Users/Matt/.julia/packages/OMEinsum/0rZnI/src/OMEinsum.jl:1
│  [5] top-level scope at /Users/Matt/.julia/packages/OMEinsum/0rZnI/src/cueinsum.jl:6
│  [6] include(::Module, ::String) at ./Base.jl:377
│  [7] include(::String) at /Users/Matt/.julia/packages/OMEinsum/0rZnI/src/OMEinsum.jl:1
│  [8] top-level scope at /Users/Matt/.julia/packages/JuliaInterpreter/jYH1M/src/construct.jl:52
│  [9] eval at ./boot.jl:331 [inlined]
│  [10] eval at /Users/Matt/.julia/packages/OMEinsum/0rZnI/src/OMEinsum.jl:1 [inlined]
│  [11] (::OMEinsum.var"#61#64")() at /Users/Matt/.julia/packages/Requires/jmibq/src/require.jl:85
│  [12] err(::Any, :

OMEinsum: YOU FIND CUDA!


┌ Error: evaluation error starting at /Users/Matt/Documents/Research/projects/ActionRNNs/jupyter/toplevel:17
│   mod = OMEinsum
│   ex = begin
    #= toplevel:17 =#
    function CuArrays.mapreducedim_kernel_serial(f, op, R, A::EinArray, range)
        #= /Users/Matt/.julia/packages/OMEinsum/0rZnI/src/cueinsum.jl:18 =#
        i = ((blockIdx()).x - 1) * (blockDim()).x + (threadIdx()).x
        #= /Users/Matt/.julia/packages/OMEinsum/0rZnI/src/cueinsum.jl:19 =#
        i > length(A.OCIS) && return nothing
        #= /Users/Matt/.julia/packages/OMEinsum/0rZnI/src/cueinsum.jl:20 =#
        #= /Users/Matt/.julia/packages/OMEinsum/0rZnI/src/cueinsum.jl:20 =# @inbounds ind_y = A.OCIS[i]
        #= /Users/Matt/.julia/packages/OMEinsum/0rZnI/src/cueinsum.jl:21 =#
        iy = subindex(A.y_indexer, ind_y.I)
        #= /Users/Matt/.julia/packages/OMEinsum/0rZnI/src/cueinsum.jl:23 =#
        #= /Users/Matt/.julia/packages/OMEinsum/0rZnI/src/cueinsum.jl:23 =# @inbounds for ind_x = A.ICIS
          

In [8]:
using Statistics, Plots, RollingFunctions, ActionRNNs, Flux
import Random

In [5]:
RWU = ActionRNNs.RingWorldUtils

ActionRNNs.RingWorldUtils

In [10]:
function construct_agent(outhorde, fc, rnn, opt, τ)


    # out_horde = RWU.gammas_term(collect(0.0:0.1:0.9))
#     out_horde = RWU.get_horde(parsed, "out")
    fs = MinimalRLCore.feature_size(fc)
#     fc, fs, chain = get_rnn_config(parsed, out_horde, rng)
    
#     opt_func = getproperty(Flux, Symbol(parsed["opt"]))
#     opt = opt_func(parsed["alpha"])

    
    ap = ActionRNNs.RandomActingPolicy([0.5, 0.5])

    ActionRNNs.FluxAgent(outhorde,
                         rnn,
                         opt,
                         τ,
                         fc,
                         fs,
                         ap)
end


construct_agent (generic function with 2 methods)

In [ ]:
fc = RWU.OneHotFeatureCreator()
fs = MinimalRLCore.feature_size(fc)
num_hidden = 6
outhorde = RWU.gammas_term(collect(0.0:0.1:0.9))

Random.seed!(10392)

rnn = Chain(
    GRU(fs, num_hidden), 
    Dense(num_hidden, num_hidden, relu),
    Dense(num_hidden, length(outhorde)))
opt = ADAM(0.0005)
τ = 8

agent = construct_agent(outhorde, fc, rnn, opt, τ)
env = RingWorld(6)

out_pred, out_err = RingWorldExperiment.experiment_loop(env, agent, "gammas_term", 300000, Random.GLOBAL_RNG; prgs=true)

Step:  88%|███████████████████████████████████████▊     |  ETA: 0:00:28

In [52]:
plot(rollmean(sqrt.(mean(out_err.^2; dims=2))[:,1], 1000))